In [1]:
%load_ext autoreload
%autoreload 2

import os
import sys
from pathlib import Path

workding_dir = str(Path.cwd().parent)
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

workding dir: /Users/inflaton/code/engd/papers/maritime/global-incidents
loading env vars from: /Users/inflaton/code/engd/papers/maritime/global-incidents/.env


True

In [2]:
import pandas as pd
import nltk
from nltk.corpus import PlaintextCorpusReader
from nltk.corpus import stopwords
from nltk.stem.porter import *
from nltk import pos_tag, word_tokenize
from nltk.stem import WordNetLemmatizer
from nltk.probability import FreqDist
from nltk.tokenize import sent_tokenize
from nltk.tokenize import word_tokenize
import contractions

import gensim
from gensim import corpora
from gensim import similarities
from gensim import models
from gensim.models import CoherenceModel

# from wordcloud import WordCloud, ImageColorGenerator
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import re
import os
import glob
import json

import pickle
from datetime import datetime
import datetime
from newspaper import Article
from gnews import GNews

In [3]:
# Function to get full news article by headline
def get_news_article(headline):
    gnews = GNews()
    articles = gnews.get_news(headline)

    if articles:
        for article in articles:
            # Assuming the headline contains the URL of the news article
            try:
                article = Article(article["url"])
                article.download()
                article.parse()
                return article.url, article.title, article.text
            except Exception as e:
                # link cannot be scraped
                # print("get_news_article - exception:", e)
                return [
                    f"cannot scrape the url: {e}",
                    "cannot scrape the title",
                    "cannot scrape the content",
                ]
    # No articles found for the given title.
    else:
        return ["no url found", "no title found", "no content found"]

In [4]:
# Read the CSV file with news titles
csv_file_path = "data/cleaned_data.csv"
df = pd.read_csv(csv_file_path)

In [5]:
df.shape

(5782, 17)

In [6]:
# drop empty news
df.dropna(subset=["Headline"], inplace=True)

In [7]:
df.shape

(5780, 17)

In [8]:
df[["Year", "Headline", "Region"]].duplicated().sum()

70

In [9]:
df_uni = df.drop_duplicates(subset=["Year", "Headline", "Region"], keep="first")
df_uni.shape

(5710, 17)

In [10]:
%%time

from tqdm import tqdm

# Iterate through each row and get the full news article
tes = df_uni

urls = []
titles = []
contents = []

for index in tqdm(range(len(tes))):
    row = tes.iloc[index]
    headline = row["Headline"]

    results = get_news_article(headline)
    urls.append(results[0])
    titles.append(results[1])
    contents.append(results[2])

# Update the DataFrame with the fetched data
tes["url"] = urls
tes["title"] = titles
tes["content"] = contents

 13%|█▎        | 757/5710 [27:31<3:29:09,  2.53s/it] /Users/inflaton/anaconda3/envs/maritime/lib/python3.12/site-packages/dateutil/parser/_parser.py:1207: UnknownTimezoneWarning: tzname PST identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "
 28%|██▊       | 1588/5710 [57:29<3:22:58,  2.95s/it] /Users/inflaton/anaconda3/envs/maritime/lib/python3.12/site-packages/dateutil/parser/_parser.py:1207: UnknownTimezoneWarning: tzname PDT identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "
 70%|██████▉   | 3978/5710 [2:27:39<1:44:23,  3.62s/it]Building prefix dict from /Users/inflaton/anaconda3/envs/maritime/lib/python3.12/site-packages/jieba/d

CPU times: user 16min 31s, sys: 3min 20s, total: 19min 51s
Wall time: 3h 30min 27s



<timed exec>:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [11]:
tes

id                                           Headline  \
0        1.0  Grasberg Mine- Grasberg mine workers extend st...   
1        2.0  Indonesia: Undersea internet cables damaged by...   
2        3.0  Shanghai port congestion impacts terminals in ...   
3        4.0  UPDATE - Indonesia: Explosion at KP Terminal i...   
4        5.0  UPDATE - Indonesia: Police confirm two explosi...   
...      ...                                                ...   
5777  5776.0  Winter storm may bring inclement weather condi...   
5778  5777.0  Winter weather expected to continue to impact ...   
5779  5778.0  Workers of Svitzer Australia plan to strike on...   
5780  5779.0  Workers stage 24-hour stoppage at DP World Ter...   
5781  5780.0  Workers with Ertsoverslagbedrijf Europoort C.V...   

                                                Details  Severity  \
0     Media sources indicate that workers at the Gra...  Moderate   
1     News sources are stating that recent typhoons ...     Minor   
2     The persisting port congestion at Shanghai’s Y...     Minor   
3     Updated local media sources from Jakarta indic...   Extreme   
4     According to local police in Jakarta, two expl...   Extreme   
...                                                 ...       ...   
5777  Intelligence received by Everstream Analytics ...  Moderate   
5778  Meteorological sources indicate that a series ...     Minor   
5779  Industry sources report on December 7 that Svi...  Moderate   
5780  Industry sources indicate on December 14 that ...  Moderate   
5781  On November 17, Dutch media sources reported t...     Minor   

                                               Category         Region  \
0                                   Mine Workers Strike      Indonesia   
1                                        Travel Warning      Indonesia   
2                                       Port Congestion          China   
3                            Bombing, Police Operations      Indonesia   
4                            Bombing, Police Operations      Indonesia   
...                                                 ...            ...   
5777                                          Ice Storm  United States   
5778  Roadway Closure / Disruption, Ground Transport...  United States   
5779                                  Industrial Action      Australia   
5780                                        Port Strike      Australia   
5781                                        Port Strike    Netherlands   

            Datetime    Year       lat        lon maritime_label  \
0      28/5/17 17:08  2017.0  -4.05608  137.11302          False   
1       4/9/17 14:30  2017.0       NaN        NaN          False   
2       27/4/17 9:16  2017.0  29.52000  121.33190           True   
3      24/5/17 15:15  2017.0  -6.22465  106.86700           True   
4      24/5/17 16:20  2017.0       NaN        NaN           True   
...              ...     ...       ...        ...            ...   
5777   16/12/20 2:47  2020.0  38.90072  -77.05440          False   
5778  31/12/20 18:15  2020.0  41.30357  -72.90561          False   
5779    7/12/20 6:16  2020.0 -38.35169  145.25050          False   
5780  14/12/20 16:52  2020.0       NaN        NaN           True   
5781  18/11/20 17:55  2020.0  51.96121    4.10550          False   

                            found_ports  contains_port_info if_labeled  Month  \
0                          ['freeport']                 1.0      False    5.0   
1                         ['hong kong']                 1.0      False    4.0   
2     ['ningbo', 'qingdao', 'shanghai']                 1.0      False    4.0   
3                           ['jakarta']                 1.0      False    5.0   
4                           ['jakarta']                 1.0       True    5.0   
...                                 ...                 ...        ...    ...   
5777                       ['new york']                 1.0      False   12.0   
5778           ['new y

In [12]:
count_rows = tes[
    ~tes["content"].isin(["cannot scrape the content", "no content found"])
].shape[0]
count_rows

3218

In [13]:
count_rows = tes[tes["content"].isin(["no content found"])].shape[0]
count_rows

2132

In [14]:
count_rows = tes[tes["content"].isin(["cannot scrape the content"])].shape[0]
count_rows

360

In [15]:
scrapped_df1 = pd.read_parquet("data/scrapped_data1.parquet")

In [16]:
scrapped_df1.shape

(5710, 20)

In [17]:
%%time

from tqdm import tqdm

urls = []
titles = []
contents = []

not_found = ["cannot scrape the content", "no content found", None]

for index in tqdm(range(len(tes))):
    row1 = scrapped_df1.iloc[index]
    row2 = tes.iloc[index]
    
    if row1["content"] in not_found and not row2["content"] in not_found and row2["title"] is not None:
        row = row2
    else:
        row = row1

    urls.append(row["url"])
    titles.append(row["title"])
    contents.append(row["content"])

# Update the DataFrame with the fetched data
tes["url"] = urls
tes["title"] = titles
tes["content"] = contents

100%|██████████| 5710/5710 [00:00<00:00, 35312.10it/s]

CPU times: user 162 ms, sys: 3.81 ms, total: 166 ms
Wall time: 165 ms



<timed exec>:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [18]:
count_rows = tes[~tes["content"].isin(not_found)].shape[0]
count_rows

3694

In [19]:
count_rows / len(tes)

0.6469352014010508

In [20]:
count_rows = tes[tes["content"].isin(["no content found"])].shape[0]
count_rows

1945

In [21]:
count_rows = tes[tes["content"].isin(["cannot scrape the content"])].shape[0]
count_rows

71

In [22]:
tes["id"] = tes["id"].astype(int)

/var/folders/7x/56svhln929zdh2xhr3mwqg4r0000gn/T/ipykernel_64033/1183224327.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tes["id"] = tes["id"].astype(int)


In [23]:
tes.to_csv("data/scrapped_data2.csv", index=False)